In [ ]:
import pandas as pd
from datetime import datetime, timedelta

In [ ]:
eur = sqlContext.sql(""" select * from dnd.pricingdf_v2_eur  """)
eur = eur.toPandas()

apa = sqlContext.sql(""" select * from dnd.pricingdf_v2_apa  """)
apa = apa.toPandas()

lam = sqlContext.sql(""" select * from dnd.pricingdf_v2_lam  """)
lam = lam.toPandas()

nam = sqlContext.sql(""" select * from dnd.pricingdf_v2_nam  """)
nam = nam.toPandas()

imea = sqlContext.sql(""" select * from dnd.pricingdf_v2_imea  """)
imea = imea.toPandas()

main_data = pd.concat([apa, eur, imea, lam, nam], ignore_index = True)
main_data.head()

Operator Pcd_Month Dipla_CD  ... Arrival-3 Arrival-2 Arrival-1
0     MAEU         9    JPNGO  ...        69        70        70
1     MAEU         9    JPNGO  ...        74        75        75
2     MAEU         9    JPNGO  ...        72        73        73
3     MAEU         9    JPNGO  ...        70        71        71
4     MAEU         9    JPNGO  ...        71        72        72

[5 rows x 20 columns]

In [ ]:
charge_cftex = pd.DataFrame()
charge=[70]
 
for start_perc in charge:
  slab_charge_percentage = start_perc
  charge_percentage = start_perc
  diff_days = 1
  diff_slabs_percent = 3
 
  column_names = ['Arrival-10','Arrival-9','Arrival-8','Arrival-7','Arrival-6','Arrival-5','Arrival-4',
                  'Arrival-3','Arrival-2','Arrival-1']
 
  df = pd.DataFrame(columns = column_names)
 
  for i in range(10,0,-2):
      for j in range(0,3):      
          Discount_Percent = slab_charge_percentage
          slab_charge_percentage = slab_charge_percentage - (slab_charge_percentage * diff_slabs_percent)/100
          df.loc['{}'.format(j+1), 'Arrival-{}'.format(i)] = round(Discount_Percent)
          df.loc['{}'.format(j+1), 'Arrival-{}'.format(i-1)] = round(Discount_Percent)
      charge_percentage += diff_days
      slab_charge_percentage = charge_percentage
 
  df['Slab'] = df.index
  df = df.reset_index().drop('index', axis=1)
  df['new_Actual_%Charge'] = start_perc
  charge_cftex = charge_cftex.append(df)
 
charge_cftex.loc[charge_cftex['Slab'] == '1', 'Slab_End_Day'] = 5
charge_cftex.loc[charge_cftex['Slab'] == '2', 'Slab_End_Day'] = 10
charge_cftex.loc[charge_cftex['Slab'] == '3', 'Slab_End_Day'] = 14
charge_cftex.head()

/root/.ipykernel/2075/command-1413856789172217-1483584403:27: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  charge_cftex = charge_cftex.append(df)


Arrival-10 Arrival-9 Arrival-8  ... Slab new_Actual_%Charge Slab_End_Day
0         70        70        71  ...    1                 70          5.0
1         68        68        69  ...    2                 70         10.0
2         66        66        67  ...    3                 70         14.0

[3 rows x 13 columns]

In [ ]:
df = pd.DataFrame(columns = ['Operator','Pcd_Month', 'Dipla_CD', 'Consignee_CD', 'Commodity','Commodity_CD', 'Cont_Size', 'Cont_Type','new_Actual_%Charge'])
for month in range(1,13,1):
  for size in [20,40]:
    new_row = {'Operator': 'MAEU','Pcd_Month': month, 'Dipla_CD':'Others', 'Consignee_CD':'Others', 'Commodity':'Others', 'Commodity_CD':'Others', 'Cont_Size':size, 'Cont_Type':'Dry', 'new_Actual_%Charge': 70}
    df.loc[len(df)] = new_row

main_data1 = df.merge(charge_cftex, on = 'new_Actual_%Charge', how='left')
main_data1 = main_data1.drop(columns = 'new_Actual_%Charge',axis = 1)
main_data1['Pcd_Month'] = main_data1['Pcd_Month'].astype(str)
main_data1['Slab'] = main_data1['Slab'].astype(int)
main_data1.tail()

Operator Pcd_Month Dipla_CD  ... Arrival-1 Slab Slab_End_Day
67     MAEU        12   Others  ...        72    2         10.0
68     MAEU        12   Others  ...        70    3         14.0
69     MAEU        12   Others  ...        74    1          5.0
70     MAEU        12   Others  ...        72    2         10.0
71     MAEU        12   Others  ...        70    3         14.0

[5 rows x 20 columns]

In [ ]:
main_data = pd.concat([main_data, main_data1]).reset_index().drop('index', axis=1)
 
main_data['Pcd_Month'] = main_data['Pcd_Month'].astype(int)
start_date = int(datetime.today().strftime('%m'))
end_date = int((datetime.today() + timedelta(days = 60)).strftime('%m'))
main_data = main_data[(main_data['Pcd_Month'] >= start_date) & (main_data['Pcd_Month'] < end_date)]
main_data['Pcd_Month'] = main_data['Pcd_Month'].astype(str)
 
main_data.tail()

Operator Pcd_Month Dipla_CD  ... Arrival-3 Arrival-2 Arrival-1
56850253     MAEU        10   Others  ...        71        72        72
56850254     MAEU        10   Others  ...        69        70        70
56850255     MAEU        10   Others  ...        73        74        74
56850256     MAEU        10   Others  ...        71        72        72
56850257     MAEU        10   Others  ...        69        70        70

[5 rows x 20 columns]

In [ ]:
pricingdf = spark.createDataFrame(main_data)
display(pricingdf)

Operator Pcd_Month Dipla_CD Consignee_CD Commodity Commodity_CD Cont_Size Cont_Type Slab Slab_End_Day Arrival-10 Arrival-9 Arrival-8 Arrival-7 Arrival-6 Arrival-5 Arrival-4 Arrival-3 Arrival-2 Arrival-1 MAEU 9 JPNGO 41500823548 Tanning extracts, dyeing extracts, paints, varnishes 0040 20 Dry 3 14.0 66 66 67 67 68 68 69 69 70 70 MAEU 9 JPNGO 41500823548 Tea and coffee 0012 20 Dry 1 5.0 71 71 72 72 73 73 74 74 75 75 MAEU 9 JPNGO 41500823548 Tea and coffee 0012 20 Dry 2 10.0 69 69 70 70 71 71 72 72 73 73 MAEU 9 JPNGO 41500823548 Tea and coffee 0012 20 Dry 3 14.0 67 67 68 68 69 69 70 70 71 71 MAEU 9 JPNGO 41500823548 Textiles and apparel 0041 20 Dry 1 5.0 68 68 69 69 70 70 71 71 72 72 MAEU 9 JPNGO 41500823548 Textiles and apparel 0041 20 Dry 2 10.0 66 66 67 67 68 68 69 69 70 70 MAEU 9 JPNGO 41500823548 Textiles and apparel 0041 20 Dry 3 14.0 64 64 65 65 66 66 67 67 68 68 MAEU 9 JPNGO 41500823548 Tile, stone and glass 0042 20 Dry 1 5.0 69 69 70 70 71 71 72 72 73 73 MAEU 9 JPNGO 41500823548 Tile, stone and glass 0042 20 Dry 2 10.0 67 67 68 68 69 69 70 70 71 71 MAEU 9 JPNGO 41500823548 Tile, stone and glass 0042 20 Dry 3 14.0 65 65 66 66 67 67 68 68 69 69 MAEU 9 JPNGO 41500823548 Vegetables 0013 20 Dry 1 5.0 71 71 72 72 73 73 74 74 75 75 MAEU 9 JPNGO 41500823548 Vegetables 0013 20 Dry 2 10.0 69 69 70 70 71 71 72 72 73 73 MAEU 9 JPNGO 41500823548 Vegetables 0013 20 Dry 3 14.0 67 67 68 68 69 69 70 70 71 71 MAEU 9 JPNGO 41500823548 Vehicles 0046 20 Dry 1 5.0 68 68 69 69 70 70 71 71 72 72 MAEU 9 JPNGO 41500823548 Vehicles 0046 20 Dry 2 10.0 66 66 67 67 68 68 69 69 70 70 MAEU 9 JPNGO 41500823548 Vehicles 0046 20 Dry 3 14.0 64 64 65 65 66 66 67 67 68 68 MAEU 9 JPNGO 41500823548 Wood 0047 20 Dry 1 5.0 64 64 65 65 66 66 67 67 68 68 MAEU 9 JPNGO 41500823548 Wood 0047 20 Dry 2 10.0 62 62 63 63 64 64 65 65 66 66 MAEU 9 JPNGO 41500823548 Wood 0047 20 Dry 3 14.0 60 60 61 61 62 62 63 63 64 64 MAEU 9 JPNGO 41500825569 Appliances and kitchenware 0014 20 Dry 1 5.0 69 69 70 70 71 71 72 72 73 73 MAEU 9 JPNGO 41500825569 Appliances and kitchenware 0014 20 Dry 2 10.0 67 67 68 68 69 69 70 70 71 71 MAEU 9 JPNGO 41500825569 Appliances and kitchenware 0014 20 Dry 3 14.0 65 65 66 66 67 67 68 68 69 69 MAEU 9 JPNGO 41500825569 Appliances and kitchenware 0014 40 Dry 1 5.0 67 67 68 68 69 69 70 70 71 71 MAEU 9 JPNGO 41500825569 Appliances and kitchenware 0014 40 Dry 2 10.0 65 65 66 66 67 67 68 68 69 69 MAEU 9 JPNGO 41500825569 Appliances and kitchenware 0014 40 Dry 3 14.0 63 63 64 64 65 65 66 66 67 67 MAEU 9 JPNGO 41500825569 Beverages 0002 40 Dry 1 5.0 68 68 69 69 70 70 71 71 72 72 MAEU 9 JPNGO 41500825569 Beverages 0002 40 Dry 2 10.0 66 66 67 67 68 68 69 69 70 70 MAEU 9 JPNGO 41500825569 Beverages 0002 40 Dry 3 14.0 64 64 65 65 66 66 67 67 68 68 MAEU 9 JPNGO 41500825569 Bone and meal 0003 20 Dry 1 5.0 71 71 72 72 73 73 74 74 75 75 MAEU 9 JPNGO 41500825569 Bone and meal 0003 20 Dry 2 10.0 69 69 70 70 71 71 72 72 73 73 MAEU 9 JPNGO 41500825569 Bone and meal 0003 20 Dry 3 14.0 67 67 68 68 69 69 70 70 71 71 MAEU 9 JPNGO 41500825569 Bone and meal 0003 40 Dry 1 5.0 69 69 70 70 71 71 72 72 73 73 MAEU 9 JPNGO 41500825569 Bone and meal 0003 40 Dry 2 10.0 67 67 68 68 69 69 70 70 71 71 MAEU 9 JPNGO 41500825569 Bone and meal 0003 40 Dry 3 14.0 65 65 66 66 67 67 68 68 69 69 MAEU 9 JPNGO 41500825569 Chemicals 0016 20 Dry 1 5.0 68 68 69 69 70 70 71 71 72 72 MAEU 9 JPNGO 41500825569 Chemicals 0016 20 Dry 2 10.0 66 66 67 67 68 68 69 69 70 70 MAEU 9 JPNGO 41500825569 Chemicals 0016 20 Dry 3 14.0 64 64 65 65 66 66 67 67 68 68 MAEU 9 JPNGO 41500825569 Chemicals 0016 40 Dry 1 5.0 69 69 70 70 71 71 72 72 73 73 MAEU 9 JPNGO 41500825569 Chemicals 0016 40 Dry 2 10.0 67 67 68 68 69 69 70 70 71 71 MAEU 9 JPNGO 41500825569 Chemicals 0016 40 Dry 3 14.0 65 65 66 66 67 67 68 68 69 69 MAEU 9 JPNGO 41500825569 Cork 0017 20 Dry 1 5.0 71 71 72 72 73 73 74 74 75 75 MAEU 9 JPNGO 41500825569 Cork 0017 20 Dry 2 10.0 69 69 70 70 71 71 72 72 73 73 MAEU 9 JPNGO 41500825569 Cork 0017 20 Dry 3 14.0 67 67 

In [ ]:
pricingdf.write.mode("overwrite").saveAsTable("dnd.pricingdf_dry_new")

In [ ]:
pricingdf = sqlContext.sql(""" select distinct * from dnd.pricingdf_dry_new  where Pcd_Month = '10' """)

In [ ]:
pricingdf.count()

19960119

In [ ]:
pricingdf = sqlContext.sql(""" select distinct * from dnd.pricingdf_dry  where Pcd_Month = '10' """)

In [ ]:
sqlschemaName= 'cng.' 

dwDatabase = 'cng_pricing'
  
dwServer =  'sqlserveridadndprod'
  
dwJdbcPort =  '1433'

dwJdbcExtraOptions =  'encrypt=true;trustServerCertificate=true;hostNameInCertificate=*.database.windows.net;loginTimeout=30;'


In [ ]:
dwUser = '****'
dwPass = '****'
dwJdbcExtraOptions = "encrypt=true;trustServerCertificate=true;hostNameInCertificate=*.database.windows.net;loginTimeout=30;"
sqlDwUrlSmall = "jdbc:sqlserver://" + dwServer + ".database.windows.net:" + dwJdbcPort + ";database=" + dwDatabase + ";user=" + dwUser+";password=" + dwPass
sqlDwhTbl="cng_pricingv1"

In [ ]:
from pyspark.sql.types import IntegerType,StringType
cftexdf = pricingdf.withColumn("Consignee_CD", pricingdf["Consignee_CD"].cast(StringType())).withColumn("Slab", pricingdf["Slab"].cast(IntegerType())).withColumn("Slab_End_Day", pricingdf["Slab_End_Day"].cast(IntegerType())).withColumn("Arrival-10", pricingdf["Arrival-10"].cast(IntegerType())).withColumn("Arrival-9", pricingdf["Arrival-9"].cast(IntegerType())).withColumn("Arrival-8", pricingdf["Arrival-8"].cast(IntegerType())).withColumn("Arrival-7", pricingdf["Arrival-7"].cast(IntegerType())).withColumn("Arrival-6", pricingdf["Arrival-6"].cast(IntegerType())).withColumn("Arrival-5", pricingdf["Arrival-5"].cast(IntegerType())).withColumn("Arrival-4", pricingdf["Arrival-4"].cast(IntegerType())).withColumn("Arrival-3", pricingdf["Arrival-3"].cast(IntegerType())).withColumn("Arrival-2", pricingdf["Arrival-2"].cast(IntegerType())).withColumn("Arrival-1", pricingdf["Arrival-1"].cast(IntegerType())).withColumn("Cont_Size", pricingdf["Cont_Size"].cast(StringType()))

In [ ]:
cftexdf.write.format("jdbc").mode("overwrite").option("truncate","true").option("BEST_EFFORT","true").option("tabLock","true").option("url", sqlDwUrlSmall).option("dbtable", sqlschemaName+sqlDwhTbl).option("user", dwUser).option("password", dwPass).option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver").save()